In [1]:
import pandas as pd
import warnings
from IPython.utils import io
import sys
import numpy as np
from datetime import datetime

warnings.filterwarnings('ignore')
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


## **Load SAS database files**

In [2]:
with io.capture_output() as captured: main_df = pd.read_sas('/Volumes/Seagate/Rush/RECENT_PROJECTS/HCRIS/hosp10-sas/prds_hosp10_yr2010.sas7bdat')
main_df = main_df.applymap(lambda x: x.decode() if isinstance(x, bytes) else x)
main_df['rpt_rec_num'] = main_df['rpt_rec_num'].astype(int)
main_df['rpt_rec_num'] = main_df['rpt_rec_num'].astype(str)
main_df = main_df.replace(r"^ +| +$", r"", regex=True)
main_df.columns = main_df.columns.str.strip()
print('2010: (rows, columns) =', main_df.shape)
print(len(main_df['prvdr_num'].unique()), main_df.shape[0], '\n')

yrs = ['2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022', '2023', '2024']
for yr in yrs:
    with io.capture_output() as captured: tdf = pd.read_sas('/Volumes/Seagate/Rush/RECENT_PROJECTS/HCRIS/hosp10-sas/prds_hosp10_yr' + yr + '.sas7bdat')
    tdf = tdf.applymap(lambda x: x.decode() if isinstance(x, bytes) else x)
    tdf['rpt_rec_num'] = tdf['rpt_rec_num'].astype(int)
    tdf['rpt_rec_num'] = tdf['rpt_rec_num'].astype(str)
    tdf = tdf.replace(r"^ +| +$", r"", regex=True)
    tdf.columns = tdf.columns.str.strip()
    main_df = pd.concat([main_df, tdf], ignore_index=True)
    print(yr + ': (rows, columns) =', main_df.shape)
    print(len(tdf['prvdr_num'].unique()), len(tdf['rpt_rec_num'].unique()), tdf.shape[0], '\n')
    #break
    
del tdf

2010: (rows, columns) = (2324, 5553)
2324 2324 

2011: (rows, columns) = (8476, 5553)
6099 6152 6152 

2012: (rows, columns) = (14703, 5553)
6132 6227 6227 

2013: (rows, columns) = (20951, 5553)
6114 6248 6248 

2014: (rows, columns) = (27201, 5553)
6123 6250 6250 

2015: (rows, columns) = (33458, 5553)
6124 6257 6257 

2016: (rows, columns) = (39669, 5553)
6107 6211 6211 

2017: (rows, columns) = (45843, 5553)
6076 6174 6174 

2018: (rows, columns) = (52004, 5553)
6049 6161 6161 

2019: (rows, columns) = (58125, 5553)
6013 6121 6121 

2020: (rows, columns) = (64184, 5553)
5989 6059 6059 

2021: (rows, columns) = (70239, 5553)
5982 6055 6055 

2022: (rows, columns) = (76305, 5553)
6001 6066 6066 

2023: (rows, columns) = (80083, 5553)
3758 3778 3778 

2024: (rows, columns) = (80104, 5553)
21 21 21 



In [3]:
prvdrs = main_df['prvdr_num'].unique().tolist()
print(len(prvdrs), 'unique CMS numbers')

names = main_df['S2_1_C1_3'].unique().tolist()
print(len(names), 'unique hospital names')

print(main_df.shape[1], 'features')
main_df.dropna(how='all', axis=1, inplace=True)
print(main_df.shape[1], 'features after removing those with no data')

7023 unique CMS numbers
9472 unique hospital names
5553 features
3928 features after removing those with no data


In [4]:
to_replace = ['rpt_rec_num', 'prvdr_num', 'fi_num', 'rpt_stus_cd', 'fi_creat_dt', 
              'fy_bgn_dt', 'fy_end_dt', 'util_cd', 'trnsmtl_num', 'state', 
              'st_cty_cd', 'census', 'region', 'proc_dt', 'msa', 'H3_1_HHA1_C10_15____',
              'H3_1_HHA1_C11_15____', 'sub3', 
             ]

replacement = ['RPT_REC_NUM', 'PRVDR_NUM', 'FI_NUM', 'RPT_STUS_CD', 'FI_CREAT_DT', 
               'FY_BGN_DT', 'FY_END_DT', 'UTIL_CODE', 'TRNSMTL_NUM', 'STATE', 
               'ST_CTY_CD', 'CENSUS', 'REGION', 'PROC_DT', 'MSA', 'H3_1_HHA1_C10_15',
               'H3_1_HHA1_C11_15', 'SUB3',
              ]

main_df.rename(columns = {to_replace[0]: replacement[0], to_replace[1]: replacement[1],
                           to_replace[2]: replacement[2], to_replace[3]: replacement[3],
                           to_replace[4]: replacement[4], to_replace[5]: replacement[5],
                           to_replace[6]: replacement[6], to_replace[7]: replacement[7],
                           to_replace[8]: replacement[8], to_replace[9]: replacement[9],
                           to_replace[10]: replacement[10], to_replace[11]: replacement[11],
                           to_replace[12]: replacement[12], to_replace[13]: replacement[13],
                           to_replace[14]: replacement[14], to_replace[15]: replacement[15],
                           to_replace[16]: replacement[16], to_replace[17]: replacement[17],
                         }, inplace = True)

print('main_df.shape:', main_df.shape)


main_df.shape: (80104, 3928)


In [5]:
# Convert 'FY_BGN_DT' to datetime format (if it's not already in datetime format)
main_df['FY_BGN_DT'] = pd.to_datetime(main_df['FY_BGN_DT'], format='%Y-%m-%d')

# Extract the year and create the new column 'Report_Period_Begin_Yr'
main_df['Report_Period_Begin_Yr'] = main_df['FY_BGN_DT'].dt.year

tdf = main_df.filter(items=['FY_BGN_DT', 'Report_Period_Begin_Yr'])
tdf.head()

FY_BGN_DT  Report_Period_Begin_Yr
0 2010-06-01                    2010
1 2010-07-01                    2010
2 2010-07-01                    2010
3 2010-07-01                    2010
4 2010-07-01                    2010

In [6]:
sas_features = list(main_df)

print('Loading machine-readable crosswalk ...\n')
crosswalk_df = pd.read_csv('~/GitHub/HCRIS-databuilder/crosswalk/2552-10 SAS FILE RECORD LAYOUT AND CROSSWALK TO 96 - 2021.csv', sep=',')
crosswalk_codes = crosswalk_df['10_FIELD_NAME'].tolist()
crosswalk_codes = [str(x).strip(' ') for x in crosswalk_codes]
crosswalk_df['10_FIELD_NAME'] = crosswalk_codes
crosswalk_df = crosswalk_df.replace(r"^ +| +$", r"", regex=True)
crosswalk_df.columns = crosswalk_df.columns.str.strip()

categories = crosswalk_df['CATEGORY'].unique().tolist()
print(len(categories), 'available cost report categories:')
print(categories, '\n')

print('Crosswalk columns:')
print('    ', list(crosswalk_df))
print('Removing unnecessary columns ...')
crosswalk_df.drop(labels=['DATA_TYPE', '96_FIELD_NAME',
                          'WKSHT CD', 'LINE', 'COLUMN'], axis=1, inplace=True)
print('Remaining columns:')
print('    ', list(crosswalk_df), '\n')

codes = crosswalk_df['10_FIELD_NAME'].tolist()
print('Number of features in the crosswalk:', len(codes))
print('Removing features not contained in SAS files ...')
crosswalk_df = crosswalk_df[crosswalk_df['10_FIELD_NAME'].isin(sas_features)]
codes = crosswalk_df['10_FIELD_NAME'].tolist()
print('Number of remaining features in the crosswalk:', len(codes))

codes = crosswalk_df['10_FIELD_NAME'].tolist()
print('Number of features in the crosswalk:', len(codes))
print('Dropping features that do not have codes ...')
crosswalk_df = crosswalk_df[~crosswalk_df['10_FIELD_NAME'].isin(['nan', np.nan, float('NaN'), 'NOT ON FORM'])]
codes = crosswalk_df['10_FIELD_NAME'].tolist()
print('Number of remaining features in the crosswalk:', len(codes))

labels = crosswalk_df['FIELD DESCRIPTION'].tolist()
print("Dropping features that do not have labels (field descriptions) ...")
crosswalk_df = crosswalk_df[~crosswalk_df['FIELD DESCRIPTION'].isin(['nan', np.nan, float('NaN'), 'NOT ON FORM'])]
labels = crosswalk_df['FIELD DESCRIPTION'].tolist()
print('Number of remaining features in the crosswalk:', len(labels))


codes = crosswalk_df['10_FIELD_NAME'].tolist()
print('Number of unique features in the crosswalk:', len(list(set(codes))))

repeated = list(set([x for x in codes if codes.count(x) > 1]))

if len(repeated) > 0:
    print('These features occur more than once:')
    print('    ', repeated)

print('\n')
print('Removing duplicates ...')
crosswalk_df.drop_duplicates(subset=['10_FIELD_NAME'], inplace=True)

codes = crosswalk_df['10_FIELD_NAME'].tolist()
repeated = list(set([x for x in codes if codes.count(x) > 1]))
if len(repeated) == 0:
    print('Duplicates removed')
print('\n')

crosswalk_codes = crosswalk_df['10_FIELD_NAME'].tolist()
print('Number of unique features in the crosswalk:', len(list(set(crosswalk_codes))))


Loading machine-readable crosswalk ...

35 available cost report categories:
['HOSPITAL IDENTIFICATION INFORMATION', nan, 'NUMBER OF BEDS', 'BED DAYS AVAILABLE', 'Medicare Inpatient Days/Outpatient Visits', 'Medicaid Inpatient Days/Outpatient Visits', 'Total Inpatient Days/Outpatient Visits', 'HOSPITAL WAGE INDEX DATA', 'HOSPITAL CONTRACT LABOR AND BENEFIT COST', 'HHA STATISTICAL DATA', 'RENAL STATISTICAL DATA', 'S-10 DATA', 'TRIAL BALANCE OF EXPENSE ACCOUNTS', 'ANALYSIS OF CHANGES IN NEW CAPITAL BALANCES', 'RECONCILIATION OF CAPITAL COST CENTERS', 'ADJUSTMENTS', 'COST ALLOCATION', 'ALLOCATION OF NEW CAPITAL COSTS', 'COMPUTATION OF RATIO OF COST TO CHARGES', 'COMPUTATION OF OUTPATIENT SERVICE COST TO CHARGE RATIOS NET OF REDUCTIONS', 'APPORTIONMENT OF INPATIENT ROUTINE SERVICE CAPITAL COSTS', 'APPORTIONMENT OF INPATIENT ANCILLARY SERVICE CAPITAL COSTS', 'APPORTIONMENT OF INPATIENT ROUTINE SERVICE OTHER PASS THROUGH COSTS', 'APPORTIONMENT OF INPATIENT/OUTPATIENT ANCILLARY SERVICE OTHER 

In [7]:
print('Number of features in the crosswalk:', len(crosswalk_codes))
print('Number of unique features in the crosswalk:', len(list(set(crosswalk_codes))))

print('Number of features in the main_df:', len(sas_features))
print('Number of unique features in the main_df:', len(list(set(sas_features))), '\n')

dif = set(sas_features).difference(crosswalk_codes)
print(len(dif), ' labels in main dataframe but not in crosswalk')

dif = set(crosswalk_codes).difference(sas_features)
print(len(dif), ' labels in crosswalk but not in main dataframe\n')

shared = list(set(sas_features) & set(crosswalk_codes))
print('Number of features shared between the main dataframe and the crosswalk:', len(shared), '\n')
shared = shared + ['Report_Period_Begin_Yr']

del sas_features
del dif

crosswalk_df = crosswalk_df[crosswalk_df['10_FIELD_NAME'].isin(shared)]
codes = crosswalk_df['10_FIELD_NAME'].tolist()
print('Removing features from crosswalk that are not in the SAS data ...')
print('Number of remaining features in crosswalk:', len(codes))
print('Number of unique remaining features in crosswalk:', len(list(set(codes))), '\n')

main_df = main_df.filter(items=shared, axis=1)
print('Removing features from main_df that are not in the crosswalk ...')
print('Number of remaining features in main_df:', len(list(main_df))-1) # not counting 'Report_Period_Begin_Yr'
print('Number of unique remaining features in main_df:', len(list(set(list(main_df))))-1) # not counting 'Report_Period_Begin_Yr'


Number of features in the crosswalk: 2836
Number of unique features in the crosswalk: 2836
Number of features in the main_df: 3929
Number of unique features in the main_df: 3929 

1093  labels in main dataframe but not in crosswalk
0  labels in crosswalk but not in main dataframe

Number of features shared between the main dataframe and the crosswalk: 2836 

Removing features from crosswalk that are not in the SAS data ...
Number of remaining features in crosswalk: 2836
Number of unique remaining features in crosswalk: 2836 

Removing features from main_df that are not in the crosswalk ...
Number of remaining features in main_df: 2836
Number of unique remaining features in main_df: 2836


In [8]:
import re 

CODE = []
FIELD_DESCRIPTION = []
TYPE = []
COMBINED_CODE_FIELD_DESCRIPTION = []


col_labels = list(main_df)

for lab in col_labels:
    if lab == 'Report_Period_Begin_Yr':
        CODE.append('Report_Period_Begin_Yr')
        FIELD_DESCRIPTION.append('Report_Period_Begin_Yr')
        TYPE.append('Report_Period_Begin_Yr')
        COMBINED_CODE_FIELD_DESCRIPTION.append('Report_Period_Begin_Yr')
    
    else:
        df_sub = crosswalk_df[crosswalk_df['10_FIELD_NAME'] == lab]
        CODE.append(df_sub['10_FIELD_NAME'].iloc[0])
        
        x1 = df_sub['FIELD DESCRIPTION'].iloc[0]
        if x1 == "" or pd.isnull(x1):
            x1 = ''
        #else:
        #    x1 = re.sub(r'[^\w\s\(\)]', '', x1.strip())
        FIELD_DESCRIPTION.append(x1)
        
        x2 = df_sub['CATEGORY'].iloc[0]
        if x2 == "" or pd.isnull(x2):
            x2 = ''
        #else:
        #    x2 = re.sub(r'[^\w\s\(\)]', '', x2.strip())
        TYPE.append(x2)
        
        x3 = df_sub['SUBCATEGORY'].iloc[0]
        if x3 == "" or pd.isnull(x3):
            x3 = ''
        #else:
        #    x3 = re.sub(r'[^\w\s\(\)]', '', x3.strip())
        
        if x1 == '' and x3 == '':
            COMBINED_CODE_FIELD_DESCRIPTION.append(lab)
        elif x1 == '':
            COMBINED_CODE_FIELD_DESCRIPTION.append(x3 + ' (' + lab + ')')
        elif x3 == '':
            COMBINED_CODE_FIELD_DESCRIPTION.append(x1 + ' (' + lab + ')')
        else:
            COMBINED_CODE_FIELD_DESCRIPTION.append(x3 + ', ' + x1 + ' (' + lab + ')')


In [9]:
df2 = pd.DataFrame([col_labels, FIELD_DESCRIPTION, TYPE, COMBINED_CODE_FIELD_DESCRIPTION], columns=col_labels)
#df2.head(10)

In [10]:
main_df = pd.concat([df2, main_df])
print(main_df.shape)

ls = np.array(main_df.iloc[[1]]).tolist()
ls = ls[0]
print(len(ls))

(80108, 2837)
2837


In [11]:
main_df.columns = pd.MultiIndex.from_arrays(main_df.iloc[0:4].values)
main_df = main_df.iloc[4:]

del col_labels
del FIELD_DESCRIPTION
del TYPE
del COMBINED_CODE_FIELD_DESCRIPTION

print(main_df.shape)
print(main_df.shape[1], 'features remaining')


(80104, 2837)
2837 features remaining


In [12]:
# 5. Shortfalls

ls1 = ['Medicaid Shortfall -- Costs minus net revenue (0 min) (S10_C1_8)',
       'Stand-alone CHIP Shortfall -- Costs minus net revenue (0 min) (S10_C1_12)',
       'State or local govt (not Medicaid or CHIP) Shortfall -- Costs minus net revenue (0 min) (S10_C1_16)',
      ]
ls2 = ['Medicaid Shortfall (S10_C1_8)',
       'Stand-alone CHIP Shortfall (S10_C1_12)',
       'State or local govt Shortfall (S10_C1_16)',
      ]

for i, l1 in enumerate(ls1):
    l2 = ls2[i]
    main_df[(l2, '', 'Financial Indicators', l2)] = main_df.loc[:, main_df.columns.get_level_values(3) == l1]


# Add engineered variables

In [13]:
tdf = main_df.copy(deep=True)

In [14]:

labs = [
    'Cost of charity care (S10_C3_23)',
    'Temporary Investments (G_C1THRU4_2)',
    'Cash on Hand and in Banks (G_C1THRU4_1)',
    'Net Patient Revenue (G3_C1_3)',
    'Depreciation, Total (A7_3_C9_3)',
    'Interest Expense (A_C2_113)',
    'Inventory (G_C1THRU4_7)',
    'Prepaid expenses (G_C1THRU4_8)',
    'Accounts Receivable (G_C1THRU4_4)',
    'Total Current Assets (G_C1THRU4_11)',
    'Total Current Liabilities (G_C1THRU4_45)',
    'Total Operating Expense (G3_C1_4)',
    'Total Assets (G_C1THRU4_36)',
    'Total Liabilities (G_C1THRU4_51)',
    'Cost To Charge Ratio (S10_C1_1)',
    'Medicaid charges (S10_C1_6)',
    'Medicaid Shortfall (S10_C1_8)',
    'Stand-alone CHIP Shortfall (S10_C1_12)',
    'State or local govt Shortfall (S10_C1_16)',
]

for l in labs:
    # Select the columns where level 4 matches the current label
    col_vals = tdf.loc[:, tdf.columns.get_level_values(3) == l]
    
    lab = list(col_vals)
    lab = lab[0]
    print(lab)
    ls = col_vals[lab].tolist()
    print('  min:', np.nanmin(ls))
    print('  No. of values < 0:', (col_vals[lab] < 0).sum().sum())
    print('  No. of values = 0:', ls.count(0))
    #print('  len:', len(ls))
    
    if l in ['Temporary Investments (G_C1THRU4_2)', 'Cash on Hand and in Banks (G_C1THRU4_1)', 'Accounts Receivable (G_C1THRU4_4)']:
        # Replace NaN values in these columns with 0
        col_vals[lab] = col_vals[lab].fillna(0)
    
    # Replace values less than 0 with 0    
    col_vals[lab] = np.where(col_vals[lab] < 0, 0, col_vals[lab])
    
    lab = list(col_vals)
    lab = lab[0]
    ls = col_vals[lab].tolist()
    print('  No. of values < 0:', (col_vals[lab] < 0).sum().sum())
    print('  No. of values = 0:', ls.count(0))
    print('  len:', len(ls), '\n')
    
    tdf[lab] = ls
    

('S10_C3_23', 'Cost of charity care', 'S-10 DATA', 'Cost of charity care (S10_C3_23)')
  min: -15617069.0
  No. of values < 0: 120
  No. of values = 0: 0
  No. of values < 0: 0
  No. of values = 0: 120
  len: 80104 

('G_C1THRU4_2', 'Temporary Investments', 'BALANCE SHEET', 'Temporary Investments (G_C1THRU4_2)')
  min: -308458746.0
  No. of values < 0: 312
  No. of values = 0: 4
  No. of values < 0: 0
  No. of values = 0: 63703
  len: 80104 

('G_C1THRU4_1', 'Cash on Hand and in Banks', 'BALANCE SHEET', 'Cash on Hand and in Banks (G_C1THRU4_1)')
  min: -3253155074.0
  No. of values < 0: 9893
  No. of values = 0: 0
  No. of values < 0: 0
  No. of values = 0: 16470
  len: 80104 

('G3_C1_3', 'Net Patient Revenue', 'STATEMENT OF REVENUES AND EXPENSES', 'Net Patient Revenue (G3_C1_3)')
  min: -1305022465.0
  No. of values < 0: 104
  No. of values = 0: 0
  No. of values < 0: 0
  No. of values = 0: 104
  len: 80104 

('A7_3_C9_3', 'Total', 'RECONCILIATION OF CAPITAL COST CENTERS', 'Depreciat

In [15]:
# ADD ENGINEERED VARIABLES

# 1. Ratio of Charity Care to Total Operating Expense
cc = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Cost of charity care (S10_C3_23)'].values.flatten().tolist())
te = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Total Operating Expense (G3_C1_4)'].values.flatten().tolist())
main_df[('Charity Care Expense Ratio', '', 'Financial Indicators', 'Charity Care Expense Ratio')] = cc/te

# 2. Total net assets
ta = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Total Assets (G_C1THRU4_36)'].values.flatten().tolist())
tl = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Total Liabilities (G_C1THRU4_51)'].values.flatten().tolist())
main_df[('Total Net Assets', '', 'Financial Indicators', 'Total Net Assets')] = ta - tl

# 3. Medicaid costs
cr = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Cost To Charge Ratio (S10_C1_1)'].values.flatten().tolist())
mc = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Medicaid charges (S10_C1_6)'].values.flatten().tolist())
main_df[('Medicaid Costs', '', 'S-10 DATA', 'Medicaid Costs')] = cr * mc


In [16]:
# 4. Cash Reserves
ti = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Temporary Investments (G_C1THRU4_2)'].values.flatten().tolist())
co = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Cash on Hand and in Banks (G_C1THRU4_1)'].values.flatten().tolist())
main_df[('Cash Reserves', '', 'Financial Indicators', 'Cash Reserves')] = ti + co


In [17]:
# MARGINS 

# From NASHP Hospital Cost Tool https://d3g6lgu1zfs2l4.cloudfront.net/

# 5. Net Profit Margin
# = Net Income / Net Patient Revenue
# = portion of Net Patient Revenue retained by the hospital.
ni = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Net Income (G3_C1_29)'].values.flatten().tolist())
nr = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Net Patient Revenue (G3_C1_3)'].values.flatten().tolist())
main_df[('Net Profit Margin', '', 'Financial Indicators', 'Net Profit Margin')] = ni / nr

# 6. Operating Profit (Loss)
# = Net Patient Revenue - Hospital Operating Costs
op = nr - te
main_df[('Operating Profit', '', 'Financial Indicators', 'Operating Profit')] = np.array(op)

# 7. Operating Profit Margin
# = Operating Profit (Loss) / Net Patient Revenue. 
# = Earnings on hospital patient services, excluding non-patient related income and costs.
main_df[('Operating Profit Margin', '', 'Financial Indicators', 'Operating Profit Margin')] = op / nr


In [18]:
# LIQUIDITY

# From https://www.investopedia.com/terms/l/liquidity.asp

# What Is Liquidity?
# Liquidity refers to the efficiency or ease with which an asset or security can be converted into ready cash without affecting its market price. The most liquid asset of all is cash itself. Consequently, the availability of cash to make such conversions is the biggest influence on whether a market can move efficiently.
# The more liquid an asset is, the easier and more efficient it is to turn it back into cash. Less liquid assets take more time and may have a higher cost.


# 8. Current Ratio
# The current ratio is the simplest and least strict. It measures current assets (those that can reasonably be converted to cash in one year) against current liabilities. Its formula would be:
# Current Ratio = Current Assets ÷ Current Liabilities
tca = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Total Current Assets (G_C1THRU4_11)'].values.flatten().tolist())
tcl = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Total Current Liabilities (G_C1THRU4_45)'].values.flatten().tolist())
main_df[('LIQUIDITY current ratio', '', 'Financial Indicators', 'LIQUIDITY current ratio')] = tca / tcl

# 9. Quick Ratio (Acid-Test Ratio)
# The quick ratio, or acid-test ratio, is slightly more strict. It excludes inventories and other current assets, which are not as liquid as cash and cash equivalents, accounts receivable, and short-term investments. The formula is:
# Quick Ratio = (Cash and Cash Equivalents + Short-Term Investments + Accounts Receivable) ÷ Current Liabilities
ar = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Accounts Receivable (G_C1THRU4_4)'].values.flatten().tolist())
main_df[('LIQUIDITY acid-test ratio', '', 'Financial Indicators', 'LIQUIDITY acid-test ratio')] = (ti + co + ar) / tcl

# 10. Acid-Test Ratio (Variation)
# A variation of the quick/acid-test ratio simply subtracts inventory from current assets, making it a bit more generous:
# Acid-Test Ratio (Variation) = (Current Assets - Inventories - Prepaid Costs) ÷ Current Liabilities
iv = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Inventory (G_C1THRU4_7)'].values.flatten().tolist())
ppe = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Prepaid expenses (G_C1THRU4_8)'].values.flatten().tolist())
main_df[('LIQUIDITY acid-test ratio (variation)', '', 'Financial Indicators', 'LIQUIDITY acid-test ratio (variation)')] = (tca - iv - ppe) / tcl

# 11. Cash Ratio
# The cash ratio is the most exacting of the liquidity ratios. Excluding accounts receivable, as well as inventories and other current assets, it defines liquid assets strictly as cash or cash equivalents.
# More than the current ratio or acid-test ratio, the cash ratio assesses an entity’s ability to stay solvent in case of an emergency—the worst-case scenario—on the grounds that even highly profitable companies can run into trouble if they do not have the liquidity to react to unforeseen events. Its formula is:
# Cash Ratio = Cash and Cash Equivalents ÷ Current Liabilities
main_df[('LIQUIDITY cash ratio', '', 'Financial Indicators', 'LIQUIDITY cash ratio')] = co / tcl


In [19]:
# SOLVENCY RATIOS

# The following metrics provide a solid solvency assessment. Each leverages different aspects of cost report data
# and provides a window into the hospital’s solvency from various angles. 

# 12. Debt-to-Equity Ratio
# Formula: Total Liabilities / (Total Net Assets or Equity)
# where Equity (Net Assets) = Total Assets − Total Liabilities
# Therefore: Debt-to-Equity Ratio = Total Liabilities / (Total Assets − Total Liabilities)
# Interpretation: This ratio indicates how much debt a facility is using to finance its assets relative to equity. A higher ratio suggests more debt relative to equity, which may indicate financial risk.
# Can also be a measure of leverage
eq = ta - tl
main_df[('Equity', '', 'Financial Indicators', 'Equity')] = np.array(eq)
main_df[('SOLVENCY Debt-to-Equity Ratio', '', 'Financial Indicators', 'SOLVENCY Debt-to-Equity Ratio')] = tl / eq


# 13. Debt Ratio
# Formula: Total Liabilities / Total Assets
# Interpretation: This ratio measures the proportion of a hospital’s assets that are financed by debt. A higher debt ratio may indicate greater financial leverage and, potentially, higher financial risk.
# Can also be a measure of leverage
main_df[('SOLVENCY Debt Ratio', '', 'Financial Indicators', 'SOLVENCY Debt Ratio')] = tl / ta


# 14. Equity Ratio
# Formula: (Total Net Assets or Equity) / Total Assets
# Interpretation: This ratio shows the proportion of assets financed by equity, representing the financial stability of the hospital. A higher ratio generally means a stronger financial position with less reliance on debt.
# Can also be a measure of leverage
main_df[('SOLVENCY Equity Ratio', '', 'Financial Indicators', 'SOLVENCY Equity Ratio')] = eq / ta


# 15. Interest Coverage Ratio
# Formula: (Operating Income + Depreciation) / Interest Expense
# Interpretation: While interest expenses may not always be separated out in CMS cost reports, 
# this ratio shows the ability to meet interest obligations with operating income, 
# providing insight into how well debt obligations are covered.
dp = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Depreciation, Total (A7_3_C9_3)'].values.flatten().tolist())
ie = np.array(tdf.loc[:, tdf.columns.get_level_values(3) == 'Interest Expense (A_C2_113)'].values.flatten().tolist())
main_df[('SOLVENCY Interest Coverage Ratio', '', 'Financial Indicators', 'SOLVENCY Interest Coverage Ratio')] = (op + dp) / ie


# From https://www.investopedia.com/terms/s/solvency.asp
# 16. Assets minus liabilities is the quickest way to assess a company’s solvency. 
# The solvency ratio calculates net income + depreciation and amortization / total liabilities. 
# This ratio is commonly used first when building out a solvency analysis.
# Note: Can't get amortization from cost reports, I think
main_df[('SOLVENCY total assets less total liabilities', '', 'Financial Indicators', 'SOLVENCY total assets less total liabilities')] = ta - tl


In [20]:
# EFFICIENCY RATIOS

# 17. Asset Turnover Ratio
# Formula: Total Revenue / Total Assets
# Interpretation: This ratio shows how efficiently the hospital uses its assets to generate revenue.
main_df[('EFFICIENCY asset turnover ratio', '', 'Financial Indicators', 'EFFICIENCY asset turnover ratio')] = nr / ta

# 18. Accounts Receivable Turnover Ratio
# Formula: Total Revenue / Patient Accounts Receivable
# Interpretation: This ratio indicates how quickly the hospital collects its receivables.
main_df[('EFFICIENCY Accounts Receivable Turnover Ratio', '', 'Financial Indicators', 'EFFICIENCY Accounts Receivable Turnover Ratio')] = nr / ar

del tdf


In [21]:
prvdrs = main_df[('PRVDR_NUM', 'Hospital Provider Number', 'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')].tolist()
print(len(prvdrs), 'hospitals in main_df')

geo_df = pd.read_pickle('~/GitHub/HCRIS-databuilder/FromCareCompare/types_and_coords.pkl')
geo_df.rename(columns={'Facility ID': 'PRVDR_NUM'}, inplace=True)
geo_df.rename(columns={'Hospital Type': 'Hospital Type (From CMS Hospitals Data Archive)'}, inplace=True)

print(list(geo_df))
print('hospitals in geo_df:', geo_df.shape[0])
print('Removing hospitals from geo_df that are not in the main_df ...')
geo_df = geo_df[geo_df['PRVDR_NUM'].isin(prvdrs)]
print('hospitals in remaining geo_df:', geo_df.shape[0])
geo_df.head()

80104 hospitals in main_df
['PRVDR_NUM', 'State', 'Hospital Type (From CMS Hospitals Data Archive)', 'Lat', 'Lon']
hospitals in geo_df: 6094
Removing hospitals from geo_df that are not in the main_df ...
hospitals in remaining geo_df: 5883


PRVDR_NUM State Hospital Type (From CMS Hospitals Data Archive)        Lat  \
0    010001    AL                            Acute Care Hospitals  31.214058   
1    010005    AL                            Acute Care Hospitals        NaN   
2    010006    AL                            Acute Care Hospitals  34.802756   
3    010007    AL                            Acute Care Hospitals  31.291972   
4    010008    AL                            Acute Care Hospitals  31.692595   

          Lon  
0  -85.361725  
1         NaN  
2  -87.652191  
3  -86.255415  
4  -86.266156

In [22]:
geo_prvdrs = geo_df['PRVDR_NUM'].tolist()

lats = []
lons = []
htypes = []

for p in prvdrs:
    
    if p in geo_prvdrs:
    
        tdf = geo_df[geo_df['PRVDR_NUM'] == p]

        lat = tdf['Lat'].iloc[0]
        lats.append(lat)

        lon = tdf['Lon'].iloc[0]
        lons.append(lon)

        htype = tdf['Hospital Type (From CMS Hospitals Data Archive)'].iloc[0]
        htypes.append(htype)
        
    else:
        lats.append(np.nan)
        lons.append(np.nan)
        htypes.append(np.nan)

tdf = main_df.copy(deep=True)
print(tdf.shape)
tdf[('Lat', 'Lat', 'Lat', 'Lat')] = lats
tdf[('Lon', 'Lon', 'Lon', 'Lon')] = lons
tdf[('Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)')] = htypes
print(tdf.shape)


(80104, 2859)
(80104, 2862)


In [23]:
main_df = tdf.copy(deep=True)
del tdf

prvdrs = main_df[('PRVDR_NUM', 'Hospital Provider Number', 
                  'HOSPITAL IDENTIFICATION INFORMATION', 
                  'Hospital Provider Number (PRVDR_NUM)')].unique().tolist()
print(len(prvdrs), 'hospitals in main_df')


7023 hospitals in main_df


In [24]:
main_df.sort_values(by=[('PRVDR_NUM', 'Hospital Provider Number', 'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)'),
                        ('Report_Period_Begin_Yr', 'Report_Period_Begin_Yr', 'Report_Period_Begin_Yr', 'Report_Period_Begin_Yr')], inplace=True, ascending=True)


In [25]:
hospital_type = main_df[('S2_1_C4_3', 'Hospital Type', '', 'Hospital Type (S2_1_C4_3)')].astype(int).tolist()
labels = []
for h in hospital_type:
    
    # from https://data.cms.gov/resources/hospital-provider-cost-report-data-dictionary
    # The number listed best corresponds with the type of services provided. 
    # 1 = General Short Term, 2 = General Long Term,  
    # 3 = Cancer,  4 = Psychiatric, 5 = Rehabilitation,  
    # 6 = Religious Non-Medical Health Care Institution, 7 = Children, 
    # 8 = Alcohol and Drug, 9 = Other.
    
    if h == 1:
        labels.append('General Short Term')
    elif h == 2:
        labels.append('General Long Term')
    elif h == 3:
        labels.append('Cancer')
    elif h == 4:
        labels.append('Psychiatric')
    elif h == 5:
        labels.append('Rehabilitation')
    elif h == 6:
        labels.append('Religious Non-Medical Health Care Institution')
    elif h == 7:
        labels.append('Children')
    elif h == 8:
        labels.append('Alcohol and Drug')
    elif h == 9:
        labels.append('Other')
    else:
        labels.append('Not given')
    

main_df[('S2_1_C4_3', 'Hospital Type', '', 'Hospital Type (S2_1_C4_3)')] = labels   


In [26]:
control_type = main_df[('S2_1_C1_21', 'Type of Control of Hospital (See Table I)', '', 'Type of Control of Hospital (See Table I) (S2_1_C1_21)')].astype(int).tolist()
labels = []
for c in control_type:
    # from https://data.cms.gov/resources/hospital-provider-cost-report-data-dictionary
    # Indicates the type of control or auspices under which the hospital is conducted as indicated: 
    # 1 = Voluntary Nonprofit-Church, 2 = Voluntary Nonprofit-Other, 
    # 3 = Proprietary-Individual, 4 = Proprietary-Corporation, 
    # 5 = Proprietary-Partnership, 6 = Proprietary-Other, 
    # 7 = Governmental- Federal, 8 = Governmental-City-County, 
    # 9 = Governmental-County, 10 = Governmental-State, 
    # 11 = Governmental-Hospital District, 
    # 12 = Governmental-City, 13 = Governmental-Other
    
    if c == 1:
        labels.append('Voluntary Nonprofit-Church')
    elif c == 2:
        labels.append('Voluntary Nonprofit-Other')
    elif c == 3:
        labels.append('Proprietary-Individual')
    elif c == 4:
        labels.append('Proprietary-Corporation')
    elif c == 5:
        labels.append('Proprietary-Partnership')
    elif c == 6:
        labels.append('Proprietary-Other')
    elif c == 7:
        labels.append('Governmental- Federal')
    elif c == 8:
        labels.append('Governmental-City-County')
    elif c == 9:
        labels.append('Governmental-County')
    elif c == 10:
        labels.append('Governmental-State')
    elif c == 11:
        labels.append('Governmental-Hospital District')
    elif c == 12:
        labels.append('Governmental-City')
    elif c == 13:
        labels.append('Governmental-Other')
    else:
        labels.append('Not given')
        
main_df[('S2_1_C1_21', 'Type of Control of Hospital (See Table I)', '', 'Type of Control of Hospital (See Table I) (S2_1_C1_21)')] = labels


In [27]:
main_df[('', 'General Ownership Type', '', 'General Ownership Type')] = main_df[('S2_1_C1_21', 'Type of Control of Hospital (See Table I)', '', 'Type of Control of Hospital (See Table I) (S2_1_C1_21)')].tolist()
main_df[('', 'General Ownership Type', '', 'General Ownership Type')] = main_df[('', 'General Ownership Type', '', 'General Ownership Type')].replace({'Voluntary Nonprofit-Other': 'non-profit',
                                           'Voluntary Nonprofit-Church': 'non-profit',
                                           'Governmental-State': 'govt',
                                           'Governmental-County': 'govt', 
                                           'Governmental-Other': 'govt', 
                                           'Governmental- Federal': 'govt', 
                                           'Governmental-Hospital District': 'govt',
                                           'Governmental-City': 'govt', 
                                           'Governmental-City-County': 'govt',
                                           'Proprietary-Corporation': 'for-profit', 
                                           'Proprietary-Partnership': 'for-profit', 
                                           'Proprietary-Other': 'for-profit',
                                           'Proprietary-Individual': 'for-profit',
                                          }, 
                                         )

print(main_df[('', 'General Ownership Type', '', 'General Ownership Type')].unique().tolist())


['govt', 'for-profit', 'non-profit']


In [28]:

medicaid_expansion_years = {
    'IN': 2015, 'FL': None, 'SC': None, 'LA': 2017, 'MN': 2014, 'TX': None, 'PA': 2015, 
    'IL': 2014, 'AZ': 2014, 'GA': None, 'ME': 2019, 'OH': 2014, 'NJ': 2014, 'NM': 2014, 
    'WV': 2014, 'OK': 2022, 'IA': 2014, 'MA': 2014, 'NY': 2014, 'PR': None, 'AR': 2014, 
    'MT': 2016, 'MO': 2021, 'WI': None, 'NC': 2024, 'KY': 2014, 'KS': None, 'MD': 2014, 
    'CA': 2014, 'HI': 2014, 'OR': 2014, 'AK': 2016, 'CT': 2014, 'NE': 2021, 'DE': 2014, 
    'NH': 2015, 'MI': 2014, 'MS': None, 'UT': 2020, 'ND': 2014, 'NV': 2014, 'AL': None, 
    'CO': 2014, 'WA': 2014, 'TN': None, 'WY': None, 'VA': 2019, 'SD': 2024, 'ID': 2020, 
    'VT': 2014, 'RI': 2014, 'DC': 2014, 'MP': None, 'VI': None, 'GU': None, 'AS': None
}

# Function to determine Medicaid Expansion status
def medicaid_expansion_status(state, yr):
    expansion_year = medicaid_expansion_years.get(state)
    if expansion_year and yr >= expansion_year:
        return 1  # Medicaid expanded
    else:
        return 0  # Medicaid not expanded or state never expanded

# Apply the function to each row in the DataFrame
c1 = ('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')
c2 = ('Report_Period_Begin_Yr', 'Report_Period_Begin_Yr', 'Report_Period_Begin_Yr', 'Report_Period_Begin_Yr')
main_df[('Medicaid Expansion State', '', 'HOSPITAL IDENTIFICATION INFORMATION', 'Medicaid Expansion State')] = main_df.apply(
    lambda row: medicaid_expansion_status(row[c1], row[c2]), axis=1)


In [29]:
main_df[('S2_1_C4_3', 'Hospital Type', '', 'Hospital Type (S2_1_C4_3)')].fillna('', inplace=True)
main_df[('Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)')].fillna('', inplace=True)

print(main_df[('S2_1_C4_3', 'Hospital Type', '', 'Hospital Type (S2_1_C4_3)')].unique())
print('\n')
print(main_df[('Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)')].unique())


['General Short Term' 'General Long Term' 'Rehabilitation' 'Children'
 'Psychiatric' 'Other' 'Cancer'
 'Religious Non-Medical Health Care Institution' 'Not given'
 'Alcohol and Drug']


['Acute Care Hospitals' '' 'Critical Access Hospitals' 'Childrens'
 'Psychiatric']


In [30]:
hcris_types = main_df[('S2_1_C4_3', 'Hospital Type', '', 'Hospital Type (S2_1_C4_3)')].tolist()
ccomp_types = main_df[('Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)', 'Hospital Type (From CMS Hospitals Data Archive)')].tolist()

combined_types = []
for i, ht in enumerate(hcris_types):
    lab = str()
    ct = ccomp_types[i]
    
    if ht == 'Not given':
        ht = ''
    if ct == 'Not given':
        ct = ''
        
    if ht == 'Other' and ct != '':
        lab = ct  
    elif ht == '' and ct == '':
        lab = 'Not given'
    elif ct == '':
        lab = ht
    elif ht == '':
        lab = ct
    else:
        lab = ht + ' (' + ct + ')'
    
    if lab == 'Children (Childrens)' or lab == 'Children':
        lab = 'Childrens'
        
    elif lab == 'Psychiatric (Psychiatric)':
        lab = 'Psychiatric'
    
    elif lab == 'Religious Non-Medical Health Care Institution':
        lab = 'Religious Non-Medical'
        
    combined_types.append(lab)
    
tdf = main_df.copy(deep=True)
tdf[('Hospital type (modified)', 'Hospital type (modified)', 'Hospital type (modified)', 'Hospital type (modified)')] = combined_types
ls = sorted(tdf[('Hospital type (modified)', 'Hospital type (modified)', 'Hospital type (modified)', 'Hospital type (modified)')].unique())
for l in ls:
    print(l)
    

print('main_df.shape:', tdf.shape)
prvdrs = tdf[('PRVDR_NUM', 'Hospital Provider Number', 'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')].unique().tolist()
print(len(prvdrs), 'hospitals in main_df')

Acute Care Hospitals
Alcohol and Drug (Critical Access Hospitals)
Cancer
Cancer (Acute Care Hospitals)
Cancer (Childrens)
Cancer (Psychiatric)
Children (Psychiatric)
Childrens
Critical Access Hospitals
General Long Term
General Long Term (Acute Care Hospitals)
General Long Term (Childrens)
General Long Term (Critical Access Hospitals)
General Long Term (Psychiatric)
General Short Term
General Short Term (Acute Care Hospitals)
General Short Term (Childrens)
General Short Term (Critical Access Hospitals)
General Short Term (Psychiatric)
Not given
Other
Psychiatric
Psychiatric (Acute Care Hospitals)
Psychiatric (Childrens)
Psychiatric (Critical Access Hospitals)
Rehabilitation
Rehabilitation (Acute Care Hospitals)
Rehabilitation (Childrens)
Rehabilitation (Psychiatric)
Religious Non-Medical
Religious Non-Medical Health Care Institution (Psychiatric)
main_df.shape: (80104, 2865)
7023 hospitals in main_df


In [31]:
main_df = tdf.copy(deep=True)
del tdf


In [32]:
# Perform customizable quick checks on hospital types

ls = main_df[('Hospital type (modified)', 'Hospital type (modified)', 
                       'Hospital type (modified)', 'Hospital type (modified)')].unique().tolist()

print(sorted(ls))
tdf = main_df[main_df[('Hospital type (modified)', 
                       'Hospital type (modified)', 
                       'Hospital type (modified)', 
                       'Hospital type (modified)')] == 'Rehabilitation (Childrens)']

print(tdf.shape)
tdf.head()

['Acute Care Hospitals', 'Alcohol and Drug (Critical Access Hospitals)', 'Cancer', 'Cancer (Acute Care Hospitals)', 'Cancer (Childrens)', 'Cancer (Psychiatric)', 'Children (Psychiatric)', 'Childrens', 'Critical Access Hospitals', 'General Long Term', 'General Long Term (Acute Care Hospitals)', 'General Long Term (Childrens)', 'General Long Term (Critical Access Hospitals)', 'General Long Term (Psychiatric)', 'General Short Term', 'General Short Term (Acute Care Hospitals)', 'General Short Term (Childrens)', 'General Short Term (Critical Access Hospitals)', 'General Short Term (Psychiatric)', 'Not given', 'Other', 'Psychiatric', 'Psychiatric (Acute Care Hospitals)', 'Psychiatric (Childrens)', 'Psychiatric (Critical Access Hospitals)', 'Rehabilitation', 'Rehabilitation (Acute Care Hospitals)', 'Rehabilitation (Childrens)', 'Rehabilitation (Psychiatric)', 'Religious Non-Medical', 'Religious Non-Medical Health Care Institution (Psychiatric)']
(21, 2865)


D_4_HOS_C3_64  \
                                                                   Intravenous Therapy   
      APPORTIONMENT OF INPATIENT/OUTPATIENT ANCILLARY SERVICE OTHER PASS THROUGH COSTS   
                                                   Intravenous Therapy (D_4_HOS_C3_64)   
58630                                                NaN                                 
64540                                                NaN                                 
74351                                                NaN                                 
79862                                                NaN                                 
79868                                                NaN                                 

                                                                        D_4_IPF_C4_200  \
                                                         Total Other Medical Education   
      APPORTIONMENT OF INPATIENT/OUTPATIENT ANCILLARY SERVICE OTHER PASS THROUGH COSTS   
                                        Total Other Medical Education (D_4_IPF_C4_200)   
58630                                                NaN                                 
64540                                                NaN                                 
74351                                                NaN                                 
79862                                                NaN                                 
79868                                                NaN                                 

                                        D3_IRF_C3_76  \
                                     Other Ancillary   
      INPATIENT ANCILLARY SERVICE COST APPORTIONMENT   
                      Other Ancillary (D3_IRF_C3_76)   
58630                                            NaN   
64540                                            NaN   
74351                                            NaN   
79862                                            NaN   
79868                                            NaN   

                                   S3_2_C2_36  \
                                    Cafeteria   
                     HOSPITAL WAGE INDEX DATA   
      AMOUNT REPORTED, Cafeteria (S3_2_C2_36)   
58630                                     NaN   
64540                                     NaN   
74351                                     NaN   
79862                                     NaN   
79868                                     NaN   

                                           S4_HHA1_C4_33  \
                             PEP Episodes:  Total Visits   
                                    HHA STATISTICAL DATA   
      HHA I, PEP Episodes:  Total Visits (S4_HHA1_C4_33)   
58630                                                NaN   
64540                                                NaN   
74351                                                NaN   
79862                                                NaN   
79868                                                NaN   

                             B_1_C21_109  \
                    Pancreas Acquisition   
                         COST ALLOCATION   
      Pancreas Acquisition (B_1_C21_109)   
58630                                NaN   
64540                                NaN   
74351                                NaN   
79862                                NaN   
79868                                NaN   

                                                A8_C2_31  \
                 Adj for Speech therapy in excess of lim   
                                             ADJUSTMENTS   
      Adj for Speech therapy in excess of lim (A8_C2_31)   
58630                                                NaN   
64540                                                NaN   
74351                                                NaN   
79862                                                NaN   
79868                                                NaN   

                         

In [33]:
del tdf

state_codes_df = pd.read_csv('~/GitHub/HCRIS-databuilder/GeoData/HCRIS_STATE_CODES.csv', sep=',')

prvdr_nums = main_df[('PRVDR_NUM', 'Hospital Provider Number', 'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')].tolist()
states1 = main_df[('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')].tolist()
states2 = []

present = 0
missing = 0
unknown = []

for i, p in enumerate(prvdr_nums):
    
    code = int(p[0:2])
    
    if code == 66:
        states2.append('MP')
        
    elif states1[i] == states1[i]:
        states2.append(states1[i])
        present += 1
        
    else:
        missing += 1
            
        tdf = state_codes_df[state_codes_df['Ssa_State_Cd'] == code]

        if tdf.shape[0] == 0:
            states2.append('UNKNOWN')
            unknown.append(p)

        else:
            state = tdf['State_Abbreviation'].iloc[0]
            states2.append(state)
        
print('unknown:', unknown)
print('present:', present)
print('missing:', missing)

tdf = main_df.copy(deep=True)
tdf[('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')] = states2

tdf = tdf.filter(items=[('PRVDR_NUM', 'Hospital Provider Number', 
                         'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)'),
                        ('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')
                        ])

print('performing check ...')

prvdr_nums = tdf[('PRVDR_NUM', 'Hospital Provider Number', 
             'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')].tolist()

ct = 0
for p in prvdr_nums:
    tdf2 = tdf[tdf[('PRVDR_NUM', 'Hospital Provider Number', 
             'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')] == p]
    states = tdf2[('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')].unique()
    if len(states) > 1:
        ct += 1
        print('hospital no.', p, 'has multiple values for their US state/territory')
        print(states, '\n')
        break

print(ct, 'hospitals with multiple values for their US state/territory')

if ct == 0:
    main_df[('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')] = states2

del tdf

print(main_df[('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')].unique())
print(main_df.shape[1], 'features in main_df')


unknown: []
present: 80094
missing: 0
performing check ...
0 hospitals with multiple values for their US state/territory
['AL' 'AK' 'AZ' 'AR' 'CA' 'CO' 'CT' 'DE' 'DC' 'FL' 'GA' 'HI' 'ID' 'IL'
 'IN' 'IA' 'KS' 'KY' 'LA' 'ME' 'MD' 'MA' 'MI' 'MN' 'MS' 'MO' 'MT' 'NE'
 'NV' 'NH' 'NJ' 'NM' 'NY' 'NC' 'ND' 'OH' 'OK' 'OR' 'PA' 'PR' 'RI' 'SC'
 'SD' 'TN' 'TX' 'UT' 'VT' 'VI' 'VA' 'WA' 'WV' 'WI' 'WY' 'AS' 'GU' 'MP']
2865 features in main_df


In [34]:
main_df[('Name and Num', 'Name and Num', 'Name and Num', 'Name and Num')] = main_df[('S2_1_C1_3', 'Hospital Name', '', 'Hospital Name (S2_1_C1_3)')].astype(str) +' (' + main_df[('PRVDR_NUM', 'Hospital Provider Number', 'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')].astype(str) + ')'   
main_df[('Name and Num', 'Name and Num', 'Name and Num', 'Name and Num')] = main_df[('Name and Num', 'Name and Num', 'Name and Num', 'Name and Num')].str.replace("#","No.")

num_name = main_df[('Name and Num', 'Name and Num', 'Name and Num', 'Name and Num')].unique()
print(len(num_name), 'unique hospital name and number combinations')

nums = main_df[('PRVDR_NUM', 'Hospital Provider Number', 'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')].unique()
print(len(nums), 'unique CMS numbers')

print(main_df.shape[1], 'features in main_df')

10195 unique hospital name and number combinations
7023 unique CMS numbers
2866 features in main_df


## Correct for inconsistent hospital names

In [35]:

nn_df = pd.read_csv('~/GitHub/HCRIS-databuilder/hospital_names_and_numbers.csv', sep=',',
                   names=['original label', 'curated label', 'CMS ID', 'CO/RN', 'SP'], header=0)

o_labs = nn_df['original label'].tolist()
c_labs = nn_df['curated label'].tolist()
nums = []

for i, o_lab in enumerate(o_labs):
    c_lab = c_labs[i]
    
    o_i = o_lab[-7:-1]
    c_i = c_lab[-7:-1]
    
    if o_i != c_i:
        print('error:', o_i, c_i)

    else:
        nums.append(o_i)
        
nn_df['CMS ID'] = nums
nn_df.sort_values(by='CMS ID', inplace=True)

print(len(nn_df['CMS ID'].unique()), 'CMS ID numbers')
print(len(nn_df['original label'].unique()), 'original name and number combinations')
print(len(nn_df['curated label'].unique()), 'curated name and number combinations')

#nn_df.to_csv('hospital_names_and_numbers.csv', index=False)
#nn_df.head()

tdf = nn_df[nn_df['CO/RN'] == 1]
ids = tdf['CMS ID'].unique()
print(len(ids), 'CMS IDs associated with names changes due to changing ownership, renaming, mergers, or closure')

tdf = nn_df[nn_df['SP'] == 1]
ids = tdf['CMS ID'].unique()
print(len(ids), 'CMS IDs associated with name variants due to slightly different spelling or typographical errors')

tdf = nn_df[(nn_df['SP'] == 1) & (nn_df['CO/RN'] == 1)]
ids = tdf['CMS ID'].unique()
print(len(ids), 'CMS IDs associated with names changes due to changing ownership, renaming, mergers, or closure AND with name variants due to slightly different spelling or typographical errors')


7024 CMS ID numbers
10202 original name and number combinations
8527 curated name and number combinations
1289 CMS IDs associated with names changes due to changing ownership, renaming, mergers, or closure
1243 CMS IDs associated with name variants due to slightly different spelling or typographical errors
286 CMS IDs associated with names changes due to changing ownership, renaming, mergers, or closure AND with name variants due to slightly different spelling or typographical errors


In [36]:
import numpy as np

o_labs = nn_df['original label'].tolist()
c_labs = nn_df['curated label'].tolist()

print('Not in list:')
new_nns = []
ct = 0
for nn1 in main_df[('Name and Num', 'Name and Num', 'Name and Num', 'Name and Num')].tolist():
    nn2 = str()
    
    try:
        i = o_labs.index(nn1)
        nn2 = c_labs[i]
    except:
        print(nn1)
        nn2 = str(nn1)
    
    #if nn1 != nn2 and ct < 10: # this is just to demonstrate a few naming errors that get fixed
    #    print(nn1, ' | ', nn2, '\n')
    #    ct += 1
    
    if nn2 in [np.nan, float('NaN')]:
        print('nn2:', nn2)
        break
        
    new_nns.append(nn2)
    
print('main_df.shape[0]:', main_df.shape[0])
print('len(new_nns):', len(new_nns))

main_df[('Curated Name and Num', 'Curated Name and Num', 'Curated Name and Num', 'Curated Name and Num')] = new_nns
print(main_df.shape[1], 'features in main_df')

Not in list:
main_df.shape[0]: 80104
len(new_nns): 80104
2867 features in main_df


In [37]:
tdf = main_df.copy(deep=True)

cols = ['Lat', 'Lon', 'Control type', 'Hospital type (modified)', 'Curated Name and Num']

for c in cols:
    mc = (c, c, c, c)
    
    if c == 'Control type':
        mc = ('S2_1_C1_21', 'Type of Control of Hospital (See Table I)', '', 'Type of Control of Hospital (See Table I) (S2_1_C1_21)')
    
    # shift column to first position
    col = tdf.pop(mc)
    tdf.insert(0, mc, col)
    
print(tdf.shape[1], 'features in main_df')
tdf.head()

2867 features in main_df


Curated Name and Num  \
                            Curated Name and Num   
                            Curated Name and Num   
                            Curated Name and Num   
6163   SOUTHEAST ALABAMA MEDICAL CENTER (010001)   
12694  SOUTHEAST ALABAMA MEDICAL CENTER (010001)   
18887  SOUTHEAST ALABAMA MEDICAL CENTER (010001)   
25469  SOUTHEAST ALABAMA MEDICAL CENTER (010001)   
32728  SOUTHEAST ALABAMA MEDICAL CENTER (010001)   

                        Hospital type (modified)  \
                        Hospital type (modified)   
                        Hospital type (modified)   
                        Hospital type (modified)   
6163   General Short Term (Acute Care Hospitals)   
12694  General Short Term (Acute Care Hospitals)   
18887  General Short Term (Acute Care Hospitals)   
25469  General Short Term (Acute Care Hospitals)   
32728  General Short Term (Acute Care Hospitals)   

                                                  S2_1_C1_21         Lon  \
                   Type of Control of Hospital (See Table I)         Lon   
                                                                     Lon   
      Type of Control of Hospital (See Table I) (S2_1_C1_21)         Lon   
6163                                 Governmental-County      -85.361725   
12694                                Governmental-County      -85.361725   
18887                                Governmental-County      -85.361725   
25469                                Governmental-County      -85.361725   
32728                                Governmental-County      -85.361725   

             Lat  \
             Lat   
             Lat   
             Lat   
6163   31.214058   
12694  31.214058   
18887  31.214058   
25469  31.214058   
32728  31.214058   

                                                                         D_4_HOS_C3_64  \
                                                                   Intravenous Therapy   
      APPORTIONMENT OF INPATIENT/OUTPATIENT ANCILLARY SERVICE OTHER PASS THROUGH COSTS   
                                                   Intravenous Therapy (D_4_HOS_C3_64)   
6163                                                 NaN                                 
12694                                                NaN                                 
18887                                                NaN                                 
25469                                                NaN                                 
32728                                                NaN                                 

                                                                        D_4_IPF_C4_200  \
                                                         Total Other Medical Education   
      APPORTIONMENT OF INPATIENT/OUTPATIENT ANCILLARY SERVICE OTHER PASS THROUGH COSTS   
                                        Total Other Medical Education (D_4_IPF_C4_200)   
6163                                                 NaN                                 
12694                                                NaN                                 
18887                                                NaN                                 
25469                                                NaN                                 
32728                                                NaN                                 

                                        D3_IRF_C3_76  \
                                     Other Ancillary   
      INPATIENT ANCILLARY SERVICE COST APPORTIONMENT   
                      Other Ancillary (D3_IRF_C3_76)   
6163                                             NaN   
12694                                            NaN   
18887                                            NaN   
25469                                            NaN   
32728                                            NaN   

                                   S3_2_C2_36  \
                                    Cafeteria   

In [38]:
# Keep this in its own code chunk
main_df = tdf.copy(deep=True)
del tdf


In [39]:

tdf = main_df.filter(items=[('PRVDR_NUM', 'Hospital Provider Number', 'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)'),
                            ('Report_Period_Begin_Yr', 'Report_Period_Begin_Yr', 'Report_Period_Begin_Yr', 'Report_Period_Begin_Yr'),
                            ('Curated Name and Num', 'Curated Name and Num', 'Curated Name and Num', 'Curated Name and Num'),
                            ('Lat', 'Lat', 'Lat', 'Lat'),
                            ('Lon', 'Lon', 'Lon', 'Lon'),
                            ('S2_1_C1_21', 'Type of Control of Hospital (See Table I)', '', 'Type of Control of Hospital (See Table I) (S2_1_C1_21)'),
                            ('Hospital type (modified)', 'Hospital type (modified)', 'Hospital type (modified)', 'Hospital type (modified)'),
                            ('S3_1_C2_27', 'Beds Total Facility', 'NUMBER OF BEDS', 'Beds Total Facility (S3_1_C2_27)'),
                            ('S3_1_C2_14)', 'Beds Total Hospital', 'NUMBER OF BEDS', 'Beds Total Hospital (S3_1_C2_14)'),
                            ('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)'),
                            ('S2_1_C1_27', 'Urban (1) or Rural (2)', '', 'Urban (1) or Rural (2) (S2_1_C1_27)'),
                            ('S2_1_C1_56', 'Is this a teaching hospital or\naffiliated with a teaching hospital? (Y/N)', '', 'Is this a teaching hospital or\naffiliated with a teaching hospital? (Y/N) (S2_1_C1_56)'),
                            ], axis=1)

c1 = ('PRVDR_NUM', 'Hospital Provider Number', 'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')
c2 = ('Report_Period_Begin_Yr', 'Report_Period_Begin_Yr', 'Report_Period_Begin_Yr', 'Report_Period_Begin_Yr')
tdf.sort_values(by=[c1, c2], ascending=[True, True], inplace=True)
tdf.to_pickle('GenDat4App_p4.pkl', protocol=4)

tdf.head()

PRVDR_NUM Report_Period_Begin_Yr  \
                  Hospital Provider Number Report_Period_Begin_Yr   
       HOSPITAL IDENTIFICATION INFORMATION Report_Period_Begin_Yr   
      Hospital Provider Number (PRVDR_NUM) Report_Period_Begin_Yr   
6163                                010001                   2010   
12694                               010001                   2011   
18887                               010001                   2012   
25469                               010001                   2013   
32728                               010001                   2014   

                            Curated Name and Num        Lat         Lon  \
                            Curated Name and Num        Lat         Lon   
                            Curated Name and Num        Lat         Lon   
                            Curated Name and Num        Lat         Lon   
6163   SOUTHEAST ALABAMA MEDICAL CENTER (010001)  31.214058  -85.361725   
12694  SOUTHEAST ALABAMA MEDICAL CENTER (010001)  31.214058  -85.361725   
18887  SOUTHEAST ALABAMA MEDICAL CENTER (010001)  31.214058  -85.361725   
25469  SOUTHEAST ALABAMA MEDICAL CENTER (010001)  31.214058  -85.361725   
32728  SOUTHEAST ALABAMA MEDICAL CENTER (010001)  31.214058  -85.361725   

                                                  S2_1_C1_21  \
                   Type of Control of Hospital (See Table I)   
                                                               
      Type of Control of Hospital (See Table I) (S2_1_C1_21)   
6163                                 Governmental-County       
12694                                Governmental-County       
18887                                Governmental-County       
25469                                Governmental-County       
32728                                Governmental-County       

                        Hospital type (modified)  \
                        Hospital type (modified)   
                        Hospital type (modified)   
                        Hospital type (modified)   
6163   General Short Term (Acute Care Hospitals)   
12694  General Short Term (Acute Care Hospitals)   
18887  General Short Term (Acute Care Hospitals)   
25469  General Short Term (Acute Care Hospitals)   
32728  General Short Term (Acute Care Hospitals)   

                            S3_1_C2_27                  S2_1_C2_2  \
                   Beds Total Facility             Hospital State   
                        NUMBER OF BEDS                              
      Beds Total Facility (S3_1_C2_27) Hospital State (S2_1_C2_2)   
6163                             420.0                         AL   
12694                            420.0                         AL   
18887                            420.0                         AL   
25469                            410.0                         AL   
32728                            400.0                         AL   

                               S2_1_C1_27  \
                   Urban (1) or Rural (2)   
                                            
      Urban (1) or Rural (2) (S2_1_C1_27)   
6163                                  1.0   
12694                                 1.0   
18887                                 1.0   
25469                                 1.0   
32728                                 2.0   

                                                                                   S2_1_C1_56  
                   Is this a teaching hospital or\naffiliated with a teaching hospital? (Y/N)  
                                                                                               
      Is this a teaching hospital or\naffiliated with a teaching hospital? (Y/N) (S2_1_C1_56)  
6163                                                   N                                       
12694                                                  N                                       
18887                                                  N                             

In [40]:
del tdf

main_df[('FY_END_DT', 'Fiscal Year End Date', 'HOSPITAL IDENTIFICATION INFORMATION', 'Fiscal Year End Date (FY_END_DT)')] = pd.to_datetime(main_df[('FY_END_DT', 'Fiscal Year End Date', 'HOSPITAL IDENTIFICATION INFORMATION', 'Fiscal Year End Date (FY_END_DT)')])
main_df = main_df.sort_values(by=[('Curated Name and Num', 'Curated Name and Num', 'Curated Name and Num', 'Curated Name and Num'),
                     ('FY_END_DT', 'Fiscal Year End Date', 'HOSPITAL IDENTIFICATION INFORMATION', 'Fiscal Year End Date (FY_END_DT)')],
                     ascending=[True, True])

print(main_df.shape[1], 'features in main_df')

2867 features in main_df


In [41]:
main_df.to_pickle('HCRIS_p4.pkl.gz', protocol=4, compression='infer')

print(main_df.shape[1], 'features')
print(len(main_df[('PRVDR_NUM', 'Hospital Provider Number', 
             'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')].unique()), 'unique CMS IDs')


2867 features
7023 unique CMS IDs


In [42]:

report_categories = list(set(main_df.columns.get_level_values(2).tolist()))
report_categories = [x for x in report_categories if str(x) != 'nan']
report_categories = [x for x in report_categories if str(x) != '']
report_categories = [x for x in report_categories if str(x) != 'Report_Period_Begin_Yr']
report_categories = [x for x in report_categories if str(x) != 'Lat']
report_categories = [x for x in report_categories if str(x) != 'Lon']
report_categories = [x for x in report_categories if str(x) != 'Curated Name and Num']
report_categories = [x for x in report_categories if str(x) != 'Hospital type (modified)']
report_categories = [x for x in report_categories if str(x) != 'Hospital Type (From CMS Hospitals Data Archive)']
report_categories = [x for x in report_categories if str(x) != 'Name and Num']
report_categories = [x for x in report_categories if str(x) != 'HOSPITAL IDENTIFICATION INFORMATION']
report_categories.sort()

import csv

with open('report_categories.csv', 'w+', newline='') as OUT:
    writer = csv.writer(OUT)
    writer.writerow(report_categories)
    
    
sub_categories = list(set(main_df.columns.get_level_values(3).tolist()))
sub_categories.sort()

with open('feature_labels.csv', 'w+', newline='') as OUT:
    writer = csv.writer(OUT)
    writer.writerow(sub_categories)


In [43]:
import re

prvdr_nums = sorted(main_df[('PRVDR_NUM', 'Hospital Provider Number', 
             'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')].unique())

for i, val in enumerate(prvdr_nums):
    
    tdf = main_df[main_df[('PRVDR_NUM', 'Hospital Provider Number', 
             'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')] == val]
    
    states1 = tdf[('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')].unique()
    states2 = [x for x in states1 if x == x]
    
    if len(list(set(states2))) > 1:
        print('Error: hospital CMS number is listed as being in 2 states!')
        print('CMS #:', val)
        print(states1)
        print(states2)
        break
    
    elif len(states2) == 0:
        print('Error: No state given. Fixing ...')
        print('CMS #:', val)
        tdf2 = CMS_Gen_Info_df[CMS_Gen_Info_df['Facility ID'] == val]
        print(tdf2.shape)
        state = tdf2['State']
        print('state:', state)
        tdf[('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')] = [state] * tdf.shape[0]
        break
        
    elif len(states1) != len(states2):
        print('CMS #:', val)
        print(states1)
        print(states2)
        tdf[('S2_1_C2_2', 'Hospital State', '', 'Hospital State (S2_1_C2_2)')] = [states2[0]] * tdf.shape[0]
        
    tdf.to_csv('provider_data/' + val + '.csv')
    
    
del tdf
del main_df

# Import large data file and perform checks

In [44]:
import pandas as pd

df = pd.read_pickle('HCRIS_p4.pkl.gz')

print(df.shape)

yrs_per_id = []

ids = df[('PRVDR_NUM', 'Hospital Provider Number', 
             'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')].unique().tolist()

for i in ids:
    tdf = df[df[('PRVDR_NUM', 'Hospital Provider Number', 
             'HOSPITAL IDENTIFICATION INFORMATION', 'Hospital Provider Number (PRVDR_NUM)')] == i]

    yrs = tdf.shape[0]
    yrs_per_id.append(yrs)
    

(80104, 2867)


In [45]:
import numpy as np

print(np.nanmean(yrs_per_id), ',', np.nanstd(yrs_per_id))
print('max:', np.nanmax(yrs_per_id))
print('min:', np.nanmin(yrs_per_id))

ct = 0
for i in [12, 13, 14, 15, 16]:
    ct += yrs_per_id.count(i)
    
print(ct, 'IDs with 12 or more years of data')

11.405951872419195 , 3.5034945474629535
max: 17
min: 1
5405 IDs with 12 or more years of data


In [46]:
sub_categories = list(set(df.columns.get_level_values(3).tolist()))
sub_categories.sort()

print(len(sub_categories))

2867


In [47]:
report_categories = list(set(df.columns.get_level_values(2).tolist()))
report_categories = [x for x in report_categories if str(x) != 'nan']
report_categories = [x for x in report_categories if str(x) != '']
report_categories = [x for x in report_categories if str(x) != 'Report_Period_Begin_Yr']
report_categories = [x for x in report_categories if str(x) != 'Lat']
report_categories = [x for x in report_categories if str(x) != 'Lon']
report_categories = [x for x in report_categories if str(x) != 'Curated Name and Num']
report_categories = [x for x in report_categories if str(x) != 'Hospital type (modified)']
report_categories = [x for x in report_categories if str(x) != 'Hospital Type (From CMS Hospitals Data Archive)']
report_categories = [x for x in report_categories if str(x) != 'Name and Num']
report_categories = [x for x in report_categories if str(x) != 'HOSPITAL IDENTIFICATION INFORMATION']
report_categories.sort()

print(len(report_categories))
print(report_categories)

28
['ADJUSTMENTS', 'ALLOCATION OF NEW CAPITAL COSTS', 'ANALYSIS OF CHANGES IN NEW CAPITAL BALANCES', 'APPORTIONMENT OF INPATIENT ROUTINE SERVICE CAPITAL COSTS', 'APPORTIONMENT OF INPATIENT ROUTINE SERVICE OTHER PASS THROUGH COSTS', 'APPORTIONMENT OF INPATIENT/OUTPATIENT ANCILLARY SERVICE OTHER PASS THROUGH COSTS', 'APPORTIONMENT OF MEDICAL AND OTHER HEALTH SERVICES', 'BALANCE SHEET', 'BED DAYS AVAILABLE', 'CALCULATION OF REIMBURSEMENT SETTLEMENT', 'CALCULATION OF REIMBURSEMENT SETTLEMENT (PPS)', 'COMPUTATION OF INPATIENT OPERATING COSTS', 'COMPUTATION OF RATIO OF COST TO CHARGES', 'COST ALLOCATION', 'Financial Indicators', 'HHA STATISTICAL DATA', 'HOSPITAL WAGE INDEX DATA', 'INPATIENT ANCILLARY SERVICE COST APPORTIONMENT', 'Medicaid Inpatient Days/Outpatient Visits', 'Medicare Inpatient Days/Outpatient Visits', 'NUMBER OF BEDS', 'RECONCILIATION OF CAPITAL COST CENTERS', 'RENAL STATISTICAL DATA', 'S-10 DATA', 'STATEMENT OF PATIENT REVENUES AND OPERATING EXPENSES', 'STATEMENT OF REVENUES

In [48]:
t = 0
for rc in report_categories:
    tdf = df.iloc[:, (df.columns.get_level_values(2)==rc)]
    print(rc, ':', tdf.shape[1], 'features')
    t += tdf.shape[1]
    
print(t, 'features will be available for statistical analysis in the app')

ADJUSTMENTS : 33 features
ALLOCATION OF NEW CAPITAL COSTS : 80 features
ANALYSIS OF CHANGES IN NEW CAPITAL BALANCES : 47 features
APPORTIONMENT OF INPATIENT ROUTINE SERVICE CAPITAL COSTS : 30 features
APPORTIONMENT OF INPATIENT ROUTINE SERVICE OTHER PASS THROUGH COSTS : 15 features
APPORTIONMENT OF INPATIENT/OUTPATIENT ANCILLARY SERVICE OTHER PASS THROUGH COSTS : 410 features
APPORTIONMENT OF MEDICAL AND OTHER HEALTH SERVICES : 216 features
BALANCE SHEET : 38 features
BED DAYS AVAILABLE : 39 features
CALCULATION OF REIMBURSEMENT SETTLEMENT : 53 features
CALCULATION OF REIMBURSEMENT SETTLEMENT (PPS) : 5 features
COMPUTATION OF INPATIENT OPERATING COSTS : 43 features
COMPUTATION OF RATIO OF COST TO CHARGES : 212 features
COST ALLOCATION : 313 features
Financial Indicators : 21 features
HHA STATISTICAL DATA : 77 features
HOSPITAL WAGE INDEX DATA : 210 features
INPATIENT ANCILLARY SERVICE COST APPORTIONMENT : 312 features
Medicaid Inpatient Days/Outpatient Visits : 25 features
Medicare Inp

In [49]:
ls = ['Curated Name and Num', 
      'Hospital type (modified)', 
      'Type of Control of Hospital (See Table I) (S2_1_C1_21)',
      'General Ownership Type',
      'Hospital State (S2_1_C2_2)', 
      'Urban/Rural Indicator at beginning (S2_1_C1_26)', 
      'Fiscal Year Begin Date (FY_BGN_DT)', 
      'Fiscal Year End Date (FY_END_DT)',
      'Report_Period_Begin_Yr',
      'Cost of charity care (S10_C3_23)', 
      'Donations, Land Improvements (A7_1_C3_2)', 
      'Total Bad Debt expense (S10_C1_26)', 
      'Total Costs (C_1_C3_202)', 
      'Total Charges (C_1_C8_202)', 
      'Beds Total Hospital (S3_1_C2_14)', 
      'Intensive Care Unit (S3_1_C2_8)', 
      'Hospital Adults & Pediatrics (S3_1_C2_1)', 
      'Interim payments (E_B_HOS_C1_41)', 
      'HVBP payment adjustment amount (E_A_HOS_C1_7093)', 
      'Subtotal (E_B_HOS_C1_32)',
      'Total Hospital (S3_1_C6_14)',
      'Payment to cost ratio (E_B_HOS_C101_5)',
      'HRR adjustment amount  (E_A_HOS_C1_7094)',
      'HVBP payment adjustment amount (E_A_HOS_C1_7093)', 
      'IPPS Payment amount (unadjusted) (E_A_HOS_C1_59)',
      'HAC reduction adjustment amount (E_A_HOS_C1_7099)', 
      'IPPS Interim payment (E_A_HOS_C1_72)',
      'ADJUSTED SALARIES, Subtotal Salaries (S3_3_C4_3)',
      'Total Hospital Interns & Residents (S3_1_C10_14)', 
      'Total Facility FTEs (S3_1_C9_27)',
      'Total Hospital (S3_1_C8_14)', 
      'Total Hospital (S3_1_C3_14)', 
      'Total discharges (S3_1_C15_14)',
      'Cost of Uncompensated Care (S10_C1_30)', 
      'Total Salaries (A_C1_200)', 
      
      'Ratio of Charity Care to Total Operating Expense',
      'Total Assets (G_C1THRU4_36)',
      'Total Liabilities (G_C1THRU4_51)',
      'Total Net Assets',
      'Cost To Charge Ratio (S10_C1_1)',
      'Medicaid charges (S10_C1_6)',
      'Medicaid Costs',
      'Net Revenue from Medicaid (S10_C1_2)',
      'Medicaid Shortfall',
      'Temporary Investments (G_C1THRU4_2)',
      'Cash on Hand and in Banks (G_C1THRU4_1)',
      'Cash Reserves',
      'Net Income (G3_C1_29)',
      'Net Patient Revenue (G3_C1_3)',
      'Net Profit Margin',
      'Operating Profit',
      'Operating Profit Margin',
      'Total Current Assets (G_C1THRU4_11)',
      'Total Current Liabilities (G_C1THRU4_45)',
      'LIQUIDITY current ratio',
      'Accounts Receivable (G_C1THRU4_4)',
      'LIQUIDITY acid-test ratio',
      'Inventory (G_C1THRU4_7)',
      'Prepaid expenses (G_C1THRU4_8)',
      'LIQUIDITY acid-test ratio (variation)',
      'LIQUIDITY cash ratio',
      'SOLVENCY Debt-to-Equity Ratio',
      'SOLVENCY Debt Ratio',
      'SOLVENCY Equity Ratio',
      'Depreciation, Total (A7_3_C9_3)',
      'Interest Expense (A_C2_113)',
      'SOLVENCY Interest Coverage Ratio',
      'SOLVENCY total assets less total liabilities',
      'EFFICIENCY asset turnover ratio',
      'EFFICIENCY Accounts Receivable Turnover Ratio',
     ]

filtered_df = df[df.columns[df.columns.get_level_values(3).isin(ls)]]
print(filtered_df.shape)

#date_condition = pd.to_datetime('2010-01-01')
filtered_df = filtered_df.reset_index(drop=True)
#filtered_df = filtered_df[filtered_df[('FY_BGN_DT', 'Fiscal Year Begin Date', 'HOSPITAL IDENTIFICATION INFORMATION', 'Fiscal Year Begin Date (FY_BGN_DT)')] >= date_condition]
filtered_df.columns = filtered_df.columns.droplevel([0, 1])
new_level = filtered_df.columns.get_level_values(0) + ': ' + filtered_df.columns.get_level_values(1)
filtered_df.columns = filtered_df.columns.droplevel(0)
filtered_df.columns = new_level
print(filtered_df.shape)

filtered_df.head()

(80104, 66)
(80104, 66)


Curated Name and Num: Curated Name and Num  \
0                         4C HEALTH (154035)   
1        A.G. HOLLEY STATE HOSPITAL (102000)   
2        A.G. HOLLEY STATE HOSPITAL (102000)   
3     ABBEVILLE AREA MEDICAL CENTER (421301)   
4     ABBEVILLE AREA MEDICAL CENTER (421301)   

  Hospital type (modified): Hospital type (modified)  \
0                                        Psychiatric   
1                                  General Long Term   
2                                  General Long Term   
3     General Short Term (Critical Access Hospitals)   
4     General Short Term (Critical Access Hospitals)   

  : Type of Control of Hospital (See Table I) (S2_1_C1_21)  \
0                          Voluntary Nonprofit-Other         
1                                 Governmental-State         
2                                 Governmental-State         
3                                Governmental-County         
4                                Governmental-County         

  S-10 DATA: Cost of charity care (S10_C3_23)  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                    406164.0   

  CALCULATION OF REIMBURSEMENT SETTLEMENT (PPS): HVBP payment adjustment amount (E_A_HOS_C1_7093)  \
0                                                NaN                                                
1                                                NaN                                                
2                                                NaN                                                
3                                                NaN                                                
4                                                NaN                                                

  Medicare Inpatient Days/Outpatient Visits: Total Hospital (S3_1_C6_14)  \
0                                              167.0                       
1                                              443.0                       
2                                             1546.0                       
3                                             1460.0                       
4                                             1280.0                       

  : Urban/Rural Indicator at beginning (S2_1_C1_26)  \
0                                               2.0   
1                                               1.0   
2                                               1.0   
3                                               2.0   
4                                               2.0   

  HOSPITAL IDENTIFICATION INFORMATION: Fiscal Year End Date (FY_END_DT)  \
0                                         2023-06-30                      
1                                         2011-06-30                      
2                                         2012-07-31                      
3                                         2011-09-30                      
4                                         2012-09-30                      

  HOSPITAL WAGE INDEX DATA: ADJUSTED SALARIES, Subtotal Salaries (S3_3_C4_3)  \
0                                                NaN                           
1                                                NaN                           
2                                                NaN                           
3                                                NaN                           
4                                                NaN                           

  NUMBER OF BEDS: Hospital Adults & Pediatrics (S3_1_C2_1)  \
0                                               16.0         
1                                              100.0         
2                                              100.0         
3                                               19.0         
4                                               19.0         

  ANALYS

In [50]:
filtered_df.rename(columns={
    "Curated Name and Num: Curated Name and Num": "Hospital",
    "Hospital type (modified): Hospital type (modified)": "Hospital type",
    ": Type of Control of Hospital (See Table I) (S2_1_C1_21)": "Control type",
    "Report_Period_Begin_Yr: Report_Period_Begin_Yr": "Report_Period_Begin_Yr",
    "HOSPITAL IDENTIFICATION INFORMATION: Fiscal Year Begin Date (FY_BGN_DT)": "Fiscal Year Begin Date",
    "HOSPITAL IDENTIFICATION INFORMATION: Fiscal Year End Date (FY_END_DT)": "Fiscal Year End Date",
    
    "NUMBER OF BEDS: Hospital Adults & Pediatrics (S3_1_C2_1)": "NUMBER OF BEDS: Adults & Pediatrics",
    "CALCULATION OF REIMBURSEMENT SETTLEMENT: Interim payments (E_B_HOS_C1_41)": "REIMBURSEMENT SETTLEMENT: Interim payments",
    "CALCULATION OF REIMBURSEMENT SETTLEMENT (PPS): HVBP payment adjustment amount (E_A_HOS_C1_7093)": "HVBP payment adjustment amount",
    "BED DAYS AVAILABLE: Total Hospital (S3_1_C3_14)": "BED DAYS: Total Hospital",
    "CALCULATION OF REIMBURSEMENT SETTLEMENT: Subtotal (E_B_HOS_C1_32)": "REIMBURSEMENT SETTLEMENT: Subtotal",
    "Medicare Inpatient Days/Outpatient Visits: Total Hospital (S3_1_C6_14)": "Total Days Title XVIII",
    "HOSPITAL WAGE INDEX DATA: ADJUSTED SALARIES, Subtotal Salaries (S3_3_C4_3)": "ADJUSTED SALARIES, Subtotal Salaries",
    "CALCULATION OF REIMBURSEMENT SETTLEMENT: Payment to cost ratio (E_B_HOS_C101_5)": "REIMBURSEMENT SETTLEMENT: Payment to cost ratio",
    "ANALYSIS OF CHANGES IN NEW CAPITAL BALANCES: Donations, Land Improvements (A7_1_C3_2)": "Donations, Land Improvements",
    "S-10 DATA: Cost of charity care (S10_C3_23)": "Total cost of charity care",
    "TRIAL BALANCE OF EXPENSE ACCOUNTS: Total Salaries (A_C1_200)": "Total Salaries",
    "S-10 DATA: Total Bad Debt expense (S10_C1_26)": "Total Bad Debt expense",
    "COMPUTATION OF RATIO OF COST TO CHARGES: Total Charges (C_1_C8_202)": "Total Charges",
    "S-10 DATA: Cost To Charge Ratio (S10_C1_1)": "Cost To Charge Ratio",
    "S-10 DATA: Net Revenue from Medicaid (S10_C1_2)": "Net Revenue from Medicaid",
    "CALCULATION OF REIMBURSEMENT SETTLEMENT: OPPS payments (E_B_HOS_C1_3)": "OPPS payments",
    "BALANCE SHEET: Total Liabilities (G_C1THRU4_51)": "Total Liabilities",
    "S-10 DATA: Medicaid charges (S10_C1_6)": "Medicaid charges",
    "COMPUTATION OF RATIO OF COST TO CHARGES: Total Costs (C_1_C3_202)": "Total Costs",
    "Total Inpatient Days/Outpatient Visits: Total discharges (S3_1_C15_14)": "Total discharges",
    "CALCULATION OF REIMBURSEMENT SETTLEMENT (PPS): IPPS Payment amount (unadjusted) (E_A_HOS_C1_59)": "IPPS Payment amount (unadjusted)",
    ": Hospital State (S2_1_C2_2)": "State",
    "Total Inpatient Days/Outpatient Visits: Total Hospital Interns & Residents (S3_1_C10_14)": "Number of Interns & Residents",
    "Total Inpatient Days/Outpatient Visits: Total Hospital (S3_1_C8_14)": "Total Inpatient Days",
    "NUMBER OF BEDS: Beds Total Hospital (S3_1_C2_14)": "NUMBER OF BEDS: Total Hospital",
    "S-10 DATA: Cost of Uncompensated Care (S10_C1_30)": "Cost of Uncompensated Care",
    "NUMBER OF BEDS: Intensive Care Unit (S3_1_C2_8)": "NUMBER OF BEDS: ICU",
    "Total Inpatient Days/Outpatient Visits: Total Facility FTEs (S3_1_C9_27)": "FTE Employees on Payroll",
    ": Urban/Rural Indicator at beginning (S2_1_C1_26)": "Urban (1) and Rural (2) Indicator",
    "CALCULATION OF REIMBURSEMENT SETTLEMENT (PPS): HAC reduction adjustment amount (E_A_HOS_C1_7099)": "HAC reduction adjustment amount",
    "CALCULATION OF REIMBURSEMENT SETTLEMENT (PPS): IPPS Interim payment (E_A_HOS_C1_72)": "IPPS Interim payment",
    
}, inplace=True)

filtered_df.head()

Hospital  \
0                      4C HEALTH (154035)   
1     A.G. HOLLEY STATE HOSPITAL (102000)   
2     A.G. HOLLEY STATE HOSPITAL (102000)   
3  ABBEVILLE AREA MEDICAL CENTER (421301)   
4  ABBEVILLE AREA MEDICAL CENTER (421301)   

                                    Hospital type               Control type  \
0                                     Psychiatric  Voluntary Nonprofit-Other   
1                               General Long Term         Governmental-State   
2                               General Long Term         Governmental-State   
3  General Short Term (Critical Access Hospitals)        Governmental-County   
4  General Short Term (Critical Access Hospitals)        Governmental-County   

  Total cost of charity care HVBP payment adjustment amount  \
0                        NaN                            NaN   
1                        NaN                            NaN   
2                        NaN                            NaN   
3                        NaN                            NaN   
4                   406164.0                            NaN   

  Total Days Title XVIII Urban (1) and Rural (2) Indicator  \
0                  167.0                               2.0   
1                  443.0                               1.0   
2                 1546.0                               1.0   
3                 1460.0                               2.0   
4                 1280.0                               2.0   

  Fiscal Year End Date ADJUSTED SALARIES, Subtotal Salaries  \
0           2023-06-30                                  NaN   
1           2011-06-30                                  NaN   
2           2012-07-31                                  NaN   
3           2011-09-30                                  NaN   
4           2012-09-30                                  NaN   

  NUMBER OF BEDS: Adults & Pediatrics Donations, Land Improvements  \
0                                16.0                          NaN   
1                               100.0                          NaN   
2                               100.0                          NaN   
3                                19.0                          NaN   
4                                19.0                          NaN   

  Total Liabilities  \
0         5225152.0   
1        11600664.0   
2        11600664.0   
3        12623663.0   
4        11936224.0   

  STATEMENT OF REVENUES AND EXPENSES: Net Patient Revenue (G3_C1_3)  \
0                                         27772148.0                  
1                                          5554148.0                  
2                                          5363759.0                  
3                                         29453196.0                  
4                                         30035575.0                  

  REIMBURSEMENT SETTLEMENT: Payment to cost ratio  \
0                                             NaN   
1                                             NaN   
2                                             NaN   
3                                             NaN   
4                                             NaN   

  BALANCE SHEET: Total Current Liabilities (G_C1THRU4_45) Total Salaries  \
0                                          5225152.0          19353840.0   
1                                         11600664.0           7404989.0   
2                                         11600664.0           7626819.0   
3                                          3518632.0          12469298.0   
4                                          3471814.0          13360573.0   

  STATEMENT OF REVENUES AND EXPENSES: Net Income (G3_C1_29)  \
0                                          6078279.0          
1                                         -5787979.0          
2                                         -6173123.0          
3                                           447137.0          
4                                           -59115.0          

  IPPS P

In [51]:
yrs = filtered_df['Report_Period_Begin_Yr'].unique().tolist()

for yr in yrs:
    tdf = filtered_df[filtered_df['Report_Period_Begin_Yr'] == yr] 
    tdf.to_csv('filtered_datasets/HCRIS_filtered_' + str(yr) + '.csv', index=False)


In [52]:
filtered_df.to_csv('filtered_datasets/HCRIS_filtered.csv', index=False)